# PandasのGroupByメソッドについて
Pandasにはグループ演算する仕組みのGroupByメソッドが用意されています。

グループ演算とは、分離、適用、結合を行うものです。

* データフレーム型のデータから、特定の列か行の値をキーとする
* 指定したキーで分離をする
* 分離したグループそれぞれに関数を適用
* 適用した関数を実行した結果が結合される


![代替テキスト](https://itstudio.co/sample/images/group1.png)

In [56]:
import pandas as pd
import numpy as np



df = pd.DataFrame({'名前':['磯野','中島','花澤','フグ田','伊佐坂'],
                   '性別':['男','男','女','女','男'],
                   '数学':np.random.randint(50,90,5),
                   '英語':np.random.randint(50,90,5)})
df

名前 性別  数学  英語
0   磯野  男  58  83
1   中島  男  77  72
2   花澤  女  53  67
3  フグ田  女  87  67
4  伊佐坂  男  67  81

## グループ化





### キーの指定方法
グループ化するキーは次のような方法で指定できます。
* リストや配列にしたキー
* データフレームの列名を示す値
* ディクショナリかシリーズ形式のもの
* 軸のインデックスまたはそれに対応した関数

## groupByメソッド
データ集約するためのGropByの最適化されたメソッドは次のものがあります。
* count：グループ内の欠損値以外の値の数
* sum：欠損値以外の合計
* mean：欠損値以外の平均
* median：欠損値以外の中央値
* std：標準偏差
* var：分散
* min：最小値
* max：最大値
* prod：欠損値以外の積
* first：欠損値以外の最初
* last：欠損値以外の最後

これ以外にも自分で定義した関数を使うこともできます。

### 実例
* 数学列でグループ化
* 英語列でグループ化

In [57]:
grouped_math = df['数学'].groupby(df['性別'])
grouped_en = df['英語'].groupby(df['性別'])
print('数学：',grouped_math.mean())
print('------------------------')
print('英語：',grouped_en.mean())

数学： 性別
女    70.000000
男    67.333333
Name: 数学, dtype: float64
------------------------
英語： 性別
女    67.000000
男    78.666667
Name: 英語, dtype: float64


In [58]:
grouped_math = df['数学'].groupby(df['性別'])
print(grouped_math)
print('----------------------')
for v in grouped_math:
  print(v)

----------------------
('女', 2    53
3    87
Name: 数学, dtype: int64)
('男', 0    58
1    77
4    67
Name: 数学, dtype: int64)


In [59]:
grouped = df[['数学','英語']].groupby(df['性別'])
grouped.mean()

数学         英語
性別                      
女   70.000000  67.000000
男   67.333333  78.666667

In [60]:
grouped = df[['数学','英語']].groupby([df['性別'],df['名前']])
grouped.mean()

数学  英語
性別 名前         
女  フグ田  87  67
   花澤   53  67
男  中島   77  72
   伊佐坂  67  81
   磯野   58  83

groupbyには列名を指定することもできます。

groupbyを指定するオブジェクトは、データフレーム型のオブジェクトを指定しておきます。この場合だとdfになります。

In [61]:
grouped = df.groupby('性別')
grouped.mean()

数学         英語
性別                      
女   70.000000  67.000000
男   67.333333  78.666667

In [62]:
grouped = df.groupby(['性別','名前'])
grouped.mean()

数学  英語
性別 名前         
女  フグ田  87  67
   花澤   53  67
男  中島   77  72
   伊佐坂  67  81
   磯野   58  83

リストでグループ化


In [73]:
grouped = df['数学'].groupby([2,1,3,5,4])
grouped.mean()

1    77
2    58
3    53
4    67
5    87
Name: 数学, dtype: int64

In [64]:
df

名前 性別  数学  英語
0   磯野  男  58  83
1   中島  男  77  72
2   花澤  女  53  67
3  フグ田  女  87  67
4  伊佐坂  男  67  81

groupby([1,1,1,2,2])とすることで、index0からindex2までを1のグループ、index3からindex4までものを2のグループにしている。

In [65]:
grouped = df['数学'].groupby([1,1,1,2,2])
# print(list(grouped))
grouped.mean()


1    62.666667
2    77.000000
Name: 数学, dtype: float64

groupedの指定配列は文字列にすることもできます。
次の例の結果は上の例と同じになります。

In [66]:
grouped = df['数学'].groupby(['a','a','a','b','b'])
# print(list(grouped))
grouped.mean()

a    62.666667
b    77.000000
Name: 数学, dtype: float64

## ディクショナリやSeriesでマッピングしてグループ化

In [67]:
record = pd.DataFrame(np.random.randint(30,80,25).reshape(5,5),
                      columns=['Japanese','Physics','English','German','Chemistry'],
                      index=['Isono','Fuguta','Nakajima','Hanazawa','Isasaka'])
record

Japanese  Physics  English  German  Chemistry
Isono           46       36       31      37         37
Fuguta          70       72       53      54         45
Nakajima        49       34       51      74         38
Hanazawa        31       74       78      37         44
Isasaka         60       52       79      48         55

マッピング用の辞書を作成

In [68]:
mapping = {'Japanese':'Language','Physics':'Science','English':'Language','German':'Language','Chemistry':'Science'}

辞書でグループ化

In [69]:
record_g = record.groupby(mapping, axis=1)
record_g.mean()

Language  Science
Isono     38.000000     36.5
Fuguta    59.000000     58.5
Nakajima  58.000000     36.0
Hanazawa  48.666667     59.0
Isasaka   62.333333     53.5

辞書をSeries化してマッピング

Seriesでもマッピングできます。(辞書と同様になる）

In [70]:
mapping_s = pd.Series(mapping)
record_gs = record.groupby(mapping_s, axis=1)
record_gs.mean()

Language  Science
Isono     38.000000     36.5
Fuguta    59.000000     58.5
Nakajima  58.000000     36.0
Hanazawa  48.666667     59.0
Isasaka   62.333333     53.5

## 関数を使ったグループ化

次の例は名前の文字数をlen関数で調べてその数で行をグループ化している。

In [71]:
record_func = record.groupby(len)
record_func.mean()

Japanese  Physics  English  German  Chemistry
5      46.0     36.0     31.0    37.0       37.0
6      70.0     72.0     53.0    54.0       45.0
7      60.0     52.0     79.0    48.0       55.0
8      40.0     54.0     64.5    55.5       41.0